## Install missing packages

In [ ]:
pip install matplotlib

In [7]:
pip install scipy

     |████████████████████████████████| 55.6 MB 2.5 MB/s eta 0:00:01
Note: you may need to restart the kernel to use updated packages.


In [6]:
pip install geopandas

  Using cached geopandas-0.10.2-py2.py3-none-any.whl (1.0 MB)
     |████████████████████████████████| 18.5 MB 2.5 MB/s eta 0:00:01
     |████████████████████████████████| 7.7 MB 2.4 MB/s eta 0:00:01
     |████████████████████████████████| 1.2 MB 3.6 MB/s eta 0:00:01
     |████████████████████████████████| 97 kB 3.3 MB/s eta 0:00:011
Note: you may need to restart the kernel to use updated packages.


In [10]:
pip install plotly

     |████████████████████████████████| 27.7 MB 2.5 MB/s eta 0:00:01
Note: you may need to restart the kernel to use updated packages.


## Import relevant libraries

In [ ]:
import pandas as pd
import scipy as sp
import geopandas as gpd
import matplotlib.pyplot as plt
import plotly.express as px

In [ ]:
import geoplotlib

def inline(width=900):
    """display the map inline in ipython
    :param width: image width for the browser
    """
    from IPython.display import Image, HTML, display, clear_output
    import random
    import string
    import urllib
    import os
    import base64

    while True:
        fname = ''.join(random.choice(string.ascii_uppercase + string.digits) for _ in range(29))
        if not os.path.isfile(fname + '.png'):
            break

    geoplotlib.savefig(fname)

    if os.path.isfile(fname + '.png'):
        with open(fname + '.png', 'rb') as fin:
            encoded = base64.b64encode(fin.read())
            b64 = urllib.parse.quote(encoded)

        image_html = "<img style='width: %dpx; margin: 0px; float: left; border: 1px solid black;' src='data:image/png;base64,%s' />" % (width, b64)

        display(HTML(image_html))
        os.remove(fname + '.png')

geoplotlib.inline = inline

In [ ]:
#Importing geoplotlib
import geoplotlib
from geoplotlib.utils import BoundingBox
from geoplotlib.utils import DataAccessObject
import json
import pandas as pd
import numpy as np
from geoplotlib.layers import BaseLayer
from geoplotlib.core import BatchPainter
from geoplotlib.utils import BoundingBox
from geoplotlib.colors import ColorMap

In [9]:
from geoplotlib.utils import read_csv
dataset = pd.read_csv('library_servicepoints.csv')
dataset = dataset.rename(columns={"SP_LAT": "lat", "SP_LONG": "lon"})

from geoplotlib.utils import DataAccessObject
dataAccess = DataAccessObject(dataset)

from geoplotlib.utils import BoundingBox
bbBC = BoundingBox.from_nominatim('AB')
geoplotlib.voronoi(dataAccess, cmap='hot_r',  alpha=200 )#, max_area=1e6)
geoplotlib.set_bbox( bbBC )
geoplotlib.inline(1000)

('bbox from Nominatim:', 48.9966667, 60.0004699, -120.0013835, -110.0047639)


2022-03-09 17:32:09.620 python[35883:1286594] Warning: Expected min height of view: (<NSPopoverTouchBarItemButton: 0x7f8f289357b0>) to be less than or equal to 30 but got a height of 32.000000. This error will be logged once per view in violation.
2022-03-09 17:32:09.621 python[35883:1286594] Warning: Expected min height of view: (<NSButton: 0x7f8f28949f30>) to be less than or equal to 30 but got a height of 32.000000. This error will be logged once per view in violation.
2022-03-09 17:32:09.624 python[35883:1286594] Warning: Expected min height of view: (<NSPopoverTouchBarItemButton: 0x7f8f2894cab0>) to be less than or equal to 30 but got a height of 32.000000. This error will be logged once per view in violation.
2022-03-09 17:32:09.626 python[35883:1286594] Warning: Expected min height of view: (<NSPopoverTouchBarItemButton: 0x7f8f28952dd0>) to be less than or equal to 30 but got a height of 32.000000. This error will be logged once per view in violation.


# choroplet

In [5]:
canada_prov = gpd.read_file('georef-canada-province.geojson')
canada_prov.dtypes

prov_type           object
prov_code           object
prov_name_fr        object
prov_name_en        object
year                object
prov_area_code      object
geometry          geometry
dtype: object

In [6]:
bmi = pd.read_csv("13100096.csv")
bmi = bmi.loc[bmi['REF_DATE'] == 2020]
bmi = bmi.loc[(bmi['GEO'] == "Alberta")|
              (bmi['GEO'] == "British Columbia")|
              (bmi['GEO'] == "Saskatchewan")|
              (bmi['GEO'] == "Manitoba")|
              (bmi['GEO'] == "Ontario")|
              (bmi['GEO'] == "Quebec")|
              (bmi['GEO'] == "New Brunswick")|
              (bmi['GEO'] == "Nova Scotia")|
              (bmi['GEO'] == "Newfoundland and Labrador")]

bmi = bmi.loc[(bmi['Sex'] == "Males")|
              (bmi['Sex'] == "Females")]

bmi = bmi.loc[(bmi['Indicators'] == "Body mass index, adjusted self-reported, adult (18 years and over), obese")]

bmi = bmi.loc[(bmi['Age group'] == "Total, 12 years and over")]

bmi = bmi.loc[(bmi['Characteristics'] == "Percent")]

#create a male df
male_bmi = bmi.loc[(bmi['Sex'] == "Males")]
male_bmi = male_bmi[['GEO','VALUE']]
male_bmi = male_bmi.rename(columns={"VALUE": "VALUE_male"})

#create a female df
female_bmi = bmi.loc[(bmi['Sex'] == "Females")]
female_bmi = female_bmi[['VALUE']]
female_bmi = female_bmi.rename(columns={"VALUE": "VALUE_female"})

male_bmi.reset_index(drop=True, inplace=True)
female_bmi.reset_index(drop=True, inplace=True)
merged_df = pd.concat([male_bmi, female_bmi], axis=1)
merged_df["ratio"] = 1-(merged_df["VALUE_male"]/merged_df["VALUE_female"])
merged_df = merged_df.rename(columns={"GEO": "prov_name_en"})
merged_df

prov_name_en  VALUE_male  VALUE_female     ratio
0  Newfoundland and Labrador        41.7          42.0  0.007143
1                Nova Scotia        36.3          35.4 -0.025424
2              New Brunswick        33.8          41.7  0.189448
3                     Quebec        26.4          26.2 -0.007634
4                    Ontario        28.5          28.4 -0.003521
5                   Manitoba        27.8          32.7  0.149847
6               Saskatchewan        35.6          31.8 -0.119497
7                    Alberta        31.4          27.9 -0.125448
8           British Columbia        24.8          22.3 -0.112108

In [18]:
#plot choropleth
fig = px.choropleth_mapbox(merged_df,
                           geojson=canada_prov,
                           color="ratio",
                           locations="prov_name_en",
                           hover_name="ratio",
                           featureidkey="properties.prov_name_en",
                           center=dict(lat=43.651070, lon=-79.347015),
                           zoom=4,
                           color_continuous_scale="thermal")

fig.update_geos(fitbounds="locations", visible=False)
fig.update_layout(margin={"r":0, "t":0, "l":0, "b":0}, mapbox_style='carto-positron')
fig.show()